# 한국어 - 영어 NMT 프로젝트

In [1]:
import os
import json
import pandas as pd
import numpy as np

# 시각화: Plotly (Static 이미지보다 분석에 유리)
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# 텍스트 처리 (추후 토크나이징 시 사용)
import re

In [2]:
import logging
import os
from datetime import datetime

# 로그 저장용 폴더 생성
os.makedirs('../logs', exist_ok=True)

# 로거 설정
logger = logging.getLogger("Mission11_NMT")
logger.setLevel(logging.INFO)

# 포맷 설정 (시간 - 이름 - 레벨 - 메시지)
formatter = logging.Formatter('%(asctime)s - %(name)s - %(levelname)s - %(message)s')

# 1. 콘솔 핸들러 (노트북 화면 출력)
stream_handler = logging.StreamHandler()
stream_handler.setFormatter(formatter)
logger.addHandler(stream_handler)

# 2. 파일 핸들러 (로그 파일 저장)
log_filename = f"../logs/train_{datetime.now().strftime('%Y%m%d_%H%M%S')}.log"
file_handler = logging.FileHandler(log_filename, encoding='utf-8')
file_handler.setFormatter(formatter)
logger.addHandler(file_handler)

logger.info("Logger 세팅 완료. 프로젝트를 시작합니다.")

2026-01-17 13:55:51,072 - Mission11_NMT - INFO - Logger 세팅 완료. 프로젝트를 시작합니다.


In [3]:
import torch

# 디바이스 설정 (Apple Silicon MPS 대응)
if torch.backends.mps.is_available():
    device = torch.device("mps")
elif torch.cuda.is_available():
    device = torch.device("cuda")
else:
    device = torch.device("cpu")

logger.info(f"Current Device: {device}")

2026-01-17 13:56:05,865 - Mission11_NMT - INFO - Current Device: cuda


In [4]:
# 경로 설정
DATA_DIR = '../data'

# 원본 JSON 경로
TRAIN_RAW = os.path.join(DATA_DIR, '일상생활및구어체_한영_train_set.json')
VALID_RAW = os.path.join(DATA_DIR, '일상생활및구어체_한영_valid_set.json')

# 저장할 피클 경로
TRAIN_CLEAN = os.path.join(DATA_DIR, 'train_set_clean.pkl')
VALID_CLEAN = os.path.join(DATA_DIR, 'valid_set_clean.pkl')

logger.info("학습 및 검증 데이터 경로 설정 완료")

2026-01-17 13:56:07,616 - Mission11_NMT - INFO - 학습 및 검증 데이터 경로 설정 완료


In [5]:
import time

def process_data(raw_path, clean_path, name="DATA"):
    """
    이 함수는 RAW 데이터를 모델 학습에 적합한 구조로 가공하고 저장하는 '파이프라인' 역할을 합니다.
    """
    start_time = time.time()
    
    if os.path.exists(clean_path):
        df = pd.read_pickle(clean_path)
        logger.info(f"[{name}] 캐시된 데이터를 로드했습니다. ({len(df):,} rows)")
    else:
        logger.info(f"[{name}] 데이터 빌드를 시작합니다... (경로: {raw_path})")
        try:
            # 원본 로드 (Heavy Task), 대용량 JSON 파일을 메모리에 로드
            with open(raw_path, 'r', encoding='utf-8') as f:
                raw_data = json.load(f)
            
            # 데이터 정규화, JSON 구조를 2차원 테이블(데이터프레임)으로 변환
            temp_df = pd.json_normalize(raw_data['data'])
            # 피처 선택, 번역에 필요한 텍스트와 분석에 필요한 메타데이터만 남김
            cols = ['domain', 'subdomain', 'ko', 'en', 'word_count_ko', 'word_count_en']
            
            # 정제: 중복 제거 및 결측치 제거
            df = temp_df[cols].drop_duplicates(subset=['ko', 'en']).dropna()
            
            # 직렬화 저장, 가공된 데이터를 바이너리 형태(피클)로 저장
            df.to_pickle(clean_path)
            duration = time.time() - start_time
            logger.info(f"[{name}] 전처리 및 피클 저장 완료. 소요 시간: {duration:.2f}s, 규모: {len(df):,} rows")
        except Exception as e:
            logger.error(f"[{name}] 처리 중 오류 발생: {str(e)}")
            raise e
            
    return df

# 학습 및 검증 데이터 각각 처리
train_df = process_data(TRAIN_RAW, TRAIN_CLEAN, "TRAIN")
valid_df = process_data(VALID_RAW, VALID_CLEAN, "VALID")

logger.info(f"전체 데이터 준비 완료. Train: {len(train_df):,}, Valid: {len(valid_df):,}")

2026-01-15 11:24:14,600 - Mission11_NMT - INFO - [TRAIN] 캐시된 데이터를 로드했습니다. (1,082,046 rows)
2026-01-15 11:24:14,754 - Mission11_NMT - INFO - [VALID] 캐시된 데이터를 로드했습니다. (141,607 rows)
2026-01-15 11:24:14,755 - Mission11_NMT - INFO - 전체 데이터 준비 완료. Train: 1,082,046, Valid: 141,607


데이터 가공 로직 및 무결성 확보
* **구조적 변환:** JSON 계층 구조를 Flattening하여 학습에 용이한 DataFrame 형태로 재구성.
* **중복성 제거:** 소스(KO)와 타겟(EN)이 모두 일치하는 중복 쌍을 제거하여 데이터 편향(Bias) 방지.
* **속도 최적화:** `json.load`의 병목 현상을 해결하기 위해 첫 실행 이후에는 `pickle` 캐시를 활용하도록 설계.

In [6]:
# 1. 도메인별 빈도 계산
train_domain = train_df['domain'].value_counts(normalize=True).reset_index()
train_domain.columns = ['domain', 'ratio']
train_domain['dataset'] = 'Train'

valid_domain = valid_df['domain'].value_counts(normalize=True).reset_index()
valid_domain.columns = ['domain', 'ratio']
valid_domain['dataset'] = 'Valid'

# 2. 데이터 통합
domain_comparison = pd.concat([train_domain, valid_domain])

# 3. Plotly Grouped Bar Chart 시각화
fig = px.bar(
    domain_comparison, 
    x='domain', 
    y='ratio', 
    color='dataset',
    barmode='group',
    text_auto='.2%',
    title="[EDA] Train vs Valid 도메인 분포 비교 (비율)",
    labels={'ratio': '비율', 'domain': '도메인'},
    color_discrete_sequence=['#636EFA', '#EF553B'] # Train(Blue), Valid(Red)
)

fig.update_layout(template="plotly_white", xaxis_tickangle=-45)
fig.show()

# 로거에 도메인 목록 기록
logger.info(f"데이터셋 포함 도메인: {train_df['domain'].unique().tolist()}")

2026-01-15 11:24:15,515 - Mission11_NMT - INFO - 데이터셋 포함 도메인: ['해외영업', '일상생활', '해외고객과의채팅']


In [7]:
# 1. 도메인별 빈도 계산 (비율로 계산하여 데이터 규모 차이에 상관없이 분포 비교)
train_domain = train_df['domain'].value_counts(normalize=True).reset_index()
train_domain.columns = ['domain', 'ratio']
train_domain['dataset'] = 'Train'

valid_domain = valid_df['domain'].value_counts(normalize=True).reset_index()
valid_domain.columns = ['domain', 'ratio']
valid_domain['dataset'] = 'Valid'

# 2. 데이터 통합
domain_comparison = pd.concat([train_domain, valid_domain])

# 3. Plotly Grouped Bar Chart 시각화
fig = px.bar(
    domain_comparison, 
    x='domain', 
    y='ratio', 
    color='dataset',
    barmode='group', # 두 데이터를 나란히 배치하여 비교 용이
    text_auto='.2%', # 막대 위에 백분율 표시
    title="[EDA] Train vs Valid 도메인 분포 비교 (비율)",
    labels={'ratio': '비율(Ratio)', 'domain': '도메인(Domain)'},
    color_discrete_sequence=['#636EFA', '#EF553B'] 
)

# 레이아웃 최적화: 글자가 겹치지 않게 하고 가독성 증대
fig.update_layout(
    template="plotly_white", 
    xaxis_tickangle=-45,
    yaxis_range=[0, 0.6], # 비율이므로 0~1 사이, 현재 데이터에 맞춰 0.6으로 설정
    legend_title_text='Dataset'
)
fig.show()

# 로거에 구체적인 도메인 구성 정보 기록
logger.info(f"Train 도메인 수: {train_df['domain'].nunique()}개")
logger.info(f"도메인 목록: {train_df['domain'].unique().tolist()}")

2026-01-15 11:24:15,680 - Mission11_NMT - INFO - Train 도메인 수: 3개
2026-01-15 11:24:15,746 - Mission11_NMT - INFO - 도메인 목록: ['해외영업', '일상생활', '해외고객과의채팅']


* **주요 도메인:** `해외영업`, `일상생활`, `해외고객과의채팅` 총 3개 그룹으로 확인됨.
* **분포 특성:** * **해외영업(약 49%):** 전체 데이터의 절반에 육박하며 가장 높은 비중을 차지함. 비즈니스 영어 번역에 특화된 모델이 될 가능성이 높음.
    * **일상생활(약 30%):** 두 번째로 높은 비중으로, 일반적인 구어체 표현이 포함됨.
    * **해외고객과의채팅(약 21%):** 상대적으로 비중은 낮으나, 실시간 메신저 스타일의 짧은 문장이 포함될 것으로 예상됨.
* **데이터 정합성:** Train과 Valid 세트의 도메인 비율 차이가 **1% 미만**으로 매우 균일함. 데이터 편향 없이 안정적인 학습 및 검증이 가능할 것으로 판단됨.


> 대분류(Domain) 수준에서는 균형이 잘 잡혀 있으나, 각 도메인 내부에 더 구체적인 상황(Subdomain)이 존재할 것으로 보임. 특히 비중이 큰 '해외영업' 내의 세부 맥락을 파악하여 모델의 범용성을 확인할 필요가 있음.

In [8]:
# 1. 서브도메인 빈도 계산
train_sub = train_df['subdomain'].value_counts().reset_index()
train_sub.columns = ['subdomain', 'count']

# 2. 시각화 (도메인별 색상 구분을 주면 더 좋습니다)
fig_sub = px.bar(
    train_sub, 
    x='count', 
    y='subdomain', 
    orientation='h', # 가로 바 차트로 가독성 확보
    title="[EDA] 서브도메인 분포 (Train)",
    labels={'count': '문장 수', 'subdomain': '서브도메인'},
    color='count', # 빈도수에 따른 색상 변화
    color_continuous_scale='Viridis'
)

fig_sub.update_layout(
    template="plotly_white", 
    yaxis={'categoryorder':'total ascending'} # 빈도순 정렬
)
fig_sub.show()

# 3. 구체적인 통계 수치 로깅
logger.info(f"전체 서브도메인 개수: {train_df['subdomain'].nunique()}개")
logger.info(f"주요 서브도메인 Top 5: {train_df['subdomain'].value_counts().head(5).index.tolist()}")

2026-01-15 11:24:15,974 - Mission11_NMT - INFO - 전체 서브도메인 개수: 11개
2026-01-15 11:24:16,025 - Mission11_NMT - INFO - 주요 서브도메인 Top 5: ['도소매유통', '음식', '여행', '연구개발,과학기술', '정보통신']


서브도메인 상세 분석 (Subdomain EDA)

분석 결과
* **서브도메인 규모:** 전체 11개의 세부 도메인으로 구성되어 있으며, 상위 5개 도메인이 전체의 상당 부분을 차지함.
* **불균형 분포:**
    * **도소매유통 (약 45만 건):** 단일 서브도메인으로서 압도적인 비중을 차지함. 상품 문의, 주문, 배송 등 이커머스/비즈니스 관련 데이터가 풍부함.
    * **음식/여행/IT:** 그 뒤를 이어 실생활 및 전문 기술 분야의 데이터가 고르게 분포되어 있음.
* **데이터 특성 인사이트:** * 대분류인 '해외영업' 내에서도 '도소매유통' 비중이 높아, 모델 학습 시 비즈니스 용어 및 수치 표현(가격, 수량 등)에 대한 처리가 중요할 것으로 보임.
    * 금융, 보험, 부동산 등 비중이 낮은 도메인에 대해서는 번역 품질이 상대적으로 낮을 수 있음을 인지해야 함.

다음 액션
> 특정 도메인(도소매유통)에 치우친 학습을 방지하기 위해, 문장 길이 분포를 확인하여 데이터의 복잡도를 파악하고 적절한 `MAX_LENGTH`를 설정함.

In [9]:
# 1. 한국어 문장 길이 분포
fig_ko = px.histogram(
    train_df, 
    x='word_count_ko', 
    nbins=100,
    title="한국어 문장 길이 분포 (단어 수)",
    labels={'word_count_ko': '단어 수', 'count': '문장 수'},
    color_discrete_sequence=['#636EFA']
)
fig_ko.update_layout(template="plotly_white", bargap=0.1)
fig_ko.show()

# 한국어 통계치 바로 확인
ko_95 = np.percentile(train_df['word_count_ko'], 95)
ko_99 = np.percentile(train_df['word_count_ko'], 99)
logger.info(f"한국어(KO) - 95% 지점: {ko_95} / 99% 지점: {ko_99}")

# ---------------------------------------------------------

# 2. 영어 문장 길이 분포
fig_en = px.histogram(
    train_df, 
    x='word_count_en', 
    nbins=100,
    title="영어 문장 길이 분포 (단어 수)",
    labels={'word_count_en': '단어 수', 'count': '문장 수'},
    color_discrete_sequence=['#EF553B']
)
fig_en.update_layout(template="plotly_white", bargap=0.1)
fig_en.show()

# 영어 통계치 바로 확인
en_95 = np.percentile(train_df['word_count_en'], 95)
en_99 = np.percentile(train_df['word_count_en'], 99)
logger.info(f"영어(EN) - 95% 지점: {en_95} / 99% 지점: {en_99}")

2026-01-15 11:24:16,140 - Mission11_NMT - INFO - 한국어(KO) - 95% 지점: 14.0 / 99% 지점: 18.0


2026-01-15 11:24:16,291 - Mission11_NMT - INFO - 영어(EN) - 95% 지점: 21.0 / 99% 지점: 27.0


문장 길이 분포 분석

* **한국어(KO):** 95%의 데이터가 단어 수 **14개** 이하이며, 99%조차 **18개** 이내에 들어옴. 문장들이 대체로 간결하고 짧은 구어체 위주임을 확인.
* **영어(EN):** 95% 지점이 **21개**, 99% 지점이 **27개**로 나타남. 한국어 대비 단어 수가 많으며, 번역 시 문장이 길어지는 경향을 반영함.
* **언어 간 상관관계:** 한국어 단어 1개당 영어 단어 약 1.5개 내외로 매칭되는 경향을 보임. 이는 추후 Attention 가중치 분석 시 참고할만한 지표가 됨.

> **MAX_LENGTH 설정:** 영어의 99% 커버리지인 27개를 고려하여, **MAX_LENGTH를 30**으로 설정함


In [10]:
def clean_text(text, lang="ko"):
    # 1. 소문자화 (영어만 해당) 및 양끝 공백 제거
    text = text.lower().strip() if lang == "en" else text.strip()
    
    # 2. 정규표현식 패턴 설정
    # 한국어: 한글, 숫자, ., !, ?, , 외 제거
    # 영어: a-z, 0-9, ., !, ?, , 외 제거
    if lang == "ko":
        pattern = r"[^가-힣0-9.!?, ]"
    else:
        pattern = r"[^a-z0-9.!?, ]"
    
    # 3. 패턴에 해당하지 않는 문자 제거
    text = re.sub(pattern, "", text)
    
    # 4. 연속된 공백 하나로 통합
    text = re.sub(r"\s+", " ", text).strip()
    
    return text

# 데이터프레임에 적용 (100만 건이므로 처리 시간이 조금 걸립니다)
start_time = time.time()
logger.info("텍스트 정제(Regex Cleaning)를 시작합니다...")

for df_name, df in [("TRAIN", train_df), ("VALID", valid_df)]:
    df['ko_clean'] = df['ko'].apply(lambda x: clean_text(x, lang="ko"))
    df['en_clean'] = df['en'].apply(lambda x: clean_text(x, lang="en"))
    logger.info(f"[{df_name}] 정제 완료")

duration = time.time() - start_time
logger.info(f"전체 정제 소요 시간: {duration:.2f}s")

# 정제 결과 샘플 확인
print("\n--- Cleaning Result Sample ---")
print(train_df[['ko', 'ko_clean', 'en', 'en_clean']].head(3))

2026-01-15 11:24:16,339 - Mission11_NMT - INFO - 텍스트 정제(Regex Cleaning)를 시작합니다...
2026-01-15 11:24:24,743 - Mission11_NMT - INFO - [TRAIN] 정제 완료
2026-01-15 11:24:25,806 - Mission11_NMT - INFO - [VALID] 정제 완료
2026-01-15 11:24:25,810 - Mission11_NMT - INFO - 전체 정제 소요 시간: 9.47s



--- Cleaning Result Sample ---
                                ko                         ko_clean  \
0  원하시는 색상을 회신해 주시면 바로 제작 들어가겠습니다.  원하시는 색상을 회신해 주시면 바로 제작 들어가겠습니다.   
1             형님 제일 웃긴 그림이 뭔지 알아요.             형님 제일 웃긴 그림이 뭔지 알아요.   
2                            >속옷을?                             속옷을?   

                                                  en  \
0  If you reply to the color you want, we will st...   
1             You know what the funniest picture is.   
2                                        >Underwear?   

                                            en_clean  
0  if you reply to the color you want, we will st...  
1             you know what the funniest picture is.  
2                                         underwear?  


텍스트 정제 (Text Cleaning)

* **노이즈 제거:** 정규표현식을 통해 한/영 필수 문장부호(`.`, `?`, `!`, `,`), 숫자, 언어별 기본 문자 외의 특수기호(`>`, `@`, `#` 등)를 제거
* **영어 정규화:** 단어 사전의 중복을 방지하기 위해 영어 문장을 소문자로 통합(Lowercasing) 처리
* **공백 최적화:** 연속된 공백을 단일화하고 문장 앞뒤의 불필요한 여백을 제거하여 데이터 일관성을 확보

In [ ]:
# 1. 필요한 라이브러리 로드 및 모델 확인
from tqdm import tqdm
from konlpy.tag import Mecab
import spacy

# Mecab 인스턴스 생성
mecab = Mecab()

# 영어 spacy 모델 로드 (없을 경우를 대비해 예외 처리)
try:
    nlp_en = spacy.load("en_core_web_sm", disable=['parser', 'ner'])
except OSError:
    logger.info("spaCy 영어 모델이 없어 설치를 시작합니다.")
    import os
    os.system("python -m spacy download en_core_web_sm")
    nlp_en = spacy.load("en_core_web_sm", disable=['parser', 'ner'])

# 2. 토큰화 함수 정의
def tokenize_ko(text):
    # 한국어: 형태소 분석 후 리스트 반환
    return mecab.morphs(text)

def tokenize_en(text):
    # 영어: 소문자화(이미 전단계에서 함) 및 단어 단위 분리
    return [token.text for token in nlp_en.tokenizer(text)]

# 3. 데이터프레임 적용 (tqdm 활용)
tqdm.pandas()

logger.info("데이터 토큰화를 시작합니다.")

for df_name, df in [("TRAIN", train_df), ("VALID", valid_df)]:
    # 한국어 토큰화
    logger.info(f"[{df_name}] 한국어 토큰화 중...")
    df['ko_tokens'] = df['ko_clean'].progress_apply(tokenize_ko)
    
    # 영어 토큰화
    logger.info(f"[{df_name}] 영어 토큰화 중...")
    df['en_tokens'] = df['en_clean'].progress_apply(tokenize_en)
    
    logger.info(f"[{df_name}] 토큰화 완료")

# 결과 샘플 확인
print("\n--- Tokenization Result Sample ---")
print(train_df[['ko_clean', 'ko_tokens', 'en_clean', 'en_tokens']].head(3))

토큰화 (Tokenization)

* **한국어(KO):** `Mecab`을 활용하여 형태소 분석 실시. `원하시는` -> `['원', '하', '시', '는']`과 같이 어근, 선어말어미, 어미를 세밀하게 분리하여 한국어의 문법적 특성을 데이터에 반영함.
* **영어(EN):** `spaCy` 토크나이저를 통해 단어와 문장부호를 분리. `underwear?` -> `['underwear', '?']`와 같이 기호를 독립 토큰화하여 모델이 의미와 문장 부호를 구분하도록 처리함.
* **성능 및 규모:** `tqdm` 모니터링 결과, 약 122만 건(Train+Valid)의 데이터를 약 50초 만에 처리 완료하여 대용량 데이터 파이프라인의 효율성을 확보함.

> **어절 vs 형태소:** 한국어 샘플 결과에서 보이듯 단순 띄어쓰기 단위보다 훨씬 세밀한 토큰화가 이루어짐. 이는 모델이 동일한 어근(`하`)에서 파생되는 다양한 활용형을 학습하는 데 유리한 구조임.

> **특수 기호 처리:** 정제 단계에서 남겨두었던 필수 문장부호(`.`, `?`, `!`)가 각 언어에서 독립된 토큰으로 잘 분리되어, 문장의 종결 어미나 어조 학습에 기여할 것으로 판단됨.

In [ ]:
from collections import Counter

def build_vocab(tokens_list, max_vocab_size=None, min_freq=2):
    """
    단어 리스트를 받아 사전(Vocab)을 구축하는 함수
    - max_vocab_size: 사전의 최대 크기
    - min_freq: 최소 등장 횟수 (이보다 적으면 <unk> 처리)
    """
    # 1. 모든 토큰의 빈도수 계산
    counter = Counter()
    for tokens in tqdm(tokens_list, desc="단어 빈도수 집계 중"):
        counter.update(tokens)
    
    # 2. 빈도수 기준 정렬 및 최소 빈도 필터링
    # 빈도가 높은 순서대로 max_vocab_size만큼만 추출
    words = [word for word, count in counter.items() if count >= min_freq]
    
    if max_vocab_size:
        # 빈도순 정렬 후 자르기
        sorted_words = sorted(counter.items(), key=lambda x: x[1], reverse=True)
        words = [word for word, count in sorted_words[:max_vocab_size] if count >= min_freq]
    
    # 3. Special Tokens 정의 (Seq2Seq 모델 필수 요소)
    # <pad>: 문장 길이를 맞추는 용도 (0순위 권장)
    # <sos>: Start Of Sequence (문장의 시작)
    # <eos>: End Of Sequence (문장의 끝)
    # <unk>: Unknown (사전에 없는 단어)
    special_tokens = ['<pad>', '<unk>', '<sos>', '<eos>']
    
    # 4. 최종 단어 리스트 구성 및 인덱스 맵핑
    vocab = special_tokens + sorted(words)
    word2idx = {word: idx for idx, word in enumerate(vocab)}
    idx2word = {idx: word for idx, word in enumerate(vocab)}
    
    return word2idx, idx2word

# --- 실행 부분 ---

logger.info("단어 사전(Vocabulary) 구축을 시작합니다.")

# 한국어 사전 (Mecab 토큰 기준)
ko_word2idx, ko_idx2word = build_vocab(train_df['ko_tokens'], min_freq=2)

# 영어 사전 (spaCy 토큰 기준)
en_word2idx, en_idx2word = build_vocab(train_df['en_tokens'], min_freq=2)

logger.info(f"한국어 단어 사전 크기: {len(ko_word2idx):,}")
logger.info(f"영어 단어 사전 크기: {len(en_word2idx):,}")

# 상위 인덱스 샘플 확인
print("\n--- Vocabulary Sample (Top 10) ---")
print(f"KO: {list(ko_word2idx.keys())[:10]}")
print(f"EN: {list(en_word2idx.keys())[:10]}")

단어 사전 구축 (Vocabulary Building)

* **빈도 기반 필터링:** 최소 2회 이상 등장한 단어들로 사전을 구성하여, 1회성 오타나 노이즈 단어를 배제하고 모델의 연산 효율을 높임.
* **Special Tokens 삽입:** 모델의 학습과 추론에 필수적인 `<pad>`(0), `<unk>`(1), `<sos>`(2), `<eos>`(3) 토큰을 사전의 최상단에 배치하여 인덱스 정합성 확보.
* **사전 규모:** * **한국어(KO):** 45,083개 토큰
    * **영어(EN):** 41,466개 토큰


> **균형 잡힌 사전 크기:** 한/영 사전 모두 4만 개 수준으로 구축됨. Embedding Layer 학습 시 메모리 부하를 줄이면서도 대부분의 구어체 표현을 커버할 수 있는 규모

> **특수 기호의 의미:** 상위 인덱스에 `!`, `.`, `...` 등 문장 부호가 다수 포함된 것은 구어체 데이터 특성상 감정 표현이나 문장 종결 방식이 다양함을 시사하며, 토크나이저가 이를 독립적으로 잘 분리했음을 재확인함.

In [ ]:
import pickle

# 저장할 데이터 묶기
preprocessing_results = {
    'train_df': train_df[['ko_clean', 'en_clean', 'ko_tokens', 'en_tokens']],
    'valid_df': valid_df[['ko_clean', 'en_clean', 'ko_tokens', 'en_tokens']],
    'ko_word2idx': ko_word2idx,
    'ko_idx2word': ko_idx2word,
    'en_word2idx': en_word2idx,
    'en_idx2word': en_idx2word,
    'max_length': 30 # 우리가 결정한 상수
}

# 최종 피클 파일 저장
FINAL_PREPROCESSED_PATH = os.path.join(DATA_DIR, 'nmt_preprocessed_final.pkl')

with open(FINAL_PREPROCESSED_PATH, 'wb') as f:
    pickle.dump(preprocessing_results, f)

logger.info(f"모든 전처리 결과가 저장되었습니다: {FINAL_PREPROCESSED_PATH}")

데이터 전처리 결과 저장 (Final Export)
* **데이터 패키징:** `train_df`, `valid_df`, `word2idx`, `idx2word` 및 `MAX_LENGTH` 설정을 하나의 딕셔너리로 통합.
* **직렬화:** `pickle` 라이브러리를 사용하여 처리된 모든 객체를 바이너리 파일(`nmt_preprocessed_final.pkl`)로 저장.

> **재사용성 확보:** 100만 건 규모의 토큰화 및 사전 구축 비용(시간 및 연산)을 1회성으로 제한하여, 이후 모델 학습 단계에서 즉각적인 데이터 로드가 가능하도록 조치함.

> **데이터 무결성:** 정제된 텍스트와 구축된 단어 사전을 함께 저장함으로써 인덱스 불일치(Mismatch) 가능성을 원천 차단함.

# 데이터셋 파이프라인 구축 (Dataset & DataLoader)

In [5]:
import torch
from torch.utils.data import Dataset, DataLoader
from torch.nn.utils.rnn import pad_sequence
import pickle
import os

FINAL_PREPROCESSED_PATH = os.path.join(DATA_DIR, 'nmt_preprocessed_final.pkl')

# 1. 전처리 결과물 로드 (전처리 단계를 패스해도 여기서 모든 정보 복원)
def load_preprocessed_data(file_path):
    if not os.path.exists(file_path):
        logger.error(f"피클 파일을 찾을 수 없습니다: {file_path}. 전처리 단계를 먼저 실행해주세요.")
        return None
    
    with open(file_path, 'rb') as f:
        data = pickle.load(f)
    logger.info(f"성공적으로 전처리 데이터를 로드했습니다. (Train: {len(data['train_df']):,} rows)")
    return data

# 파일 로드 실행
loaded_data = load_preprocessed_data(FINAL_PREPROCESSED_PATH)

if loaded_data:
    train_df = loaded_data['train_df']
    valid_df = loaded_data['valid_df']
    ko_word2idx = loaded_data['ko_word2idx']
    en_word2idx = loaded_data['en_word2idx']
    max_len = loaded_data['max_length']

# 2. PyTorch Custom Dataset 정의
class NMTDataset(Dataset):
    def __init__(self, df, src_word2idx, tar_word2idx, max_len):
        self.src_tokens = df['ko_tokens'].values
        self.tar_tokens = df['en_tokens'].values
        self.src_word2idx = src_word2idx
        self.tar_word2idx = tar_word2idx
        self.max_len = max_len

    def __len__(self):
        return len(self.src_tokens)

    def __getitem__(self, idx):
        # 한국어(Source): <sos>는 필요 없으나 관습적으로 붙이기도 함. 여기선 생략 혹은 추가 선택 가능.
        # 영어(Target): 학습 시 <sos>로 시작해서 <eos>로 끝나도록 구성 (Seq2Seq 필수)
        
        src_idx = [self.src_word2idx.get(t, self.src_word2idx['<unk>']) for t in self.src_tokens[idx]]
        tar_idx = [self.tar_word2idx['<sos>']] + \
                  [self.tar_word2idx.get(t, self.tar_word2idx['<unk>']) for t in self.tar_tokens[idx]] + \
                  [self.tar_word2idx['<eos>']]

        # 지정한 max_len까지만 슬라이싱 (안전 장치)
        return torch.tensor(src_idx[:self.max_len]), torch.tensor(tar_idx[:self.max_len+1])

# 3. Padding 처리를 위한 collate_fn (서로 다른 길이의 문장을 배치 단위로 맞춤)
def collate_fn(batch):
    src_batch, tar_batch = zip(*batch)
    # <pad> 토큰 번호인 0으로 채움
    src_batch = pad_sequence(src_batch, batch_first=True, padding_value=0)
    tar_batch = pad_sequence(tar_batch, batch_first=True, padding_value=0)
    return src_batch, tar_batch

# 4. 데이터셋 및 데이터로더 생성
BATCH_SIZE = 32 # 메모리 환경에 따라 조절 가능

train_dataset = NMTDataset(train_df, ko_word2idx, en_word2idx, max_len)
valid_dataset = NMTDataset(valid_df, ko_word2idx, en_word2idx, max_len)

train_loader = DataLoader(train_dataset, batch_size=BATCH_SIZE, shuffle=True, collate_fn=collate_fn,num_workers=0)
valid_loader = DataLoader(valid_dataset, batch_size=BATCH_SIZE, shuffle=False, collate_fn=collate_fn,num_workers=0)

logger.info(f"DataLoader 준비 완료. Batch Size: {BATCH_SIZE}")

2026-01-17 13:56:43,770 - Mission11_NMT - INFO - 성공적으로 전처리 데이터를 로드했습니다. (Train: 1,082,046 rows)
2026-01-17 13:56:43,827 - Mission11_NMT - INFO - DataLoader 준비 완료. Batch Size: 32


In [6]:
# Train/Valid 로더에서 첫 번째 배치만 꺼내서 확인
for name, loader in [("TRAIN", train_loader), ("VALID", valid_loader)]:
    src_sample, tar_sample = next(iter(loader))
    logger.info(f"[{name} Batch Sample]")
    logger.info(f" - Source Shape (KO): {src_sample.shape}") # [64, 30] 예상
    logger.info(f" - Target Shape (EN): {tar_sample.shape}") # [64, 31] (<sos>, <eos> 포함) 예상
    
    # 실제 데이터 샘플 (첫 번째 문장의 앞부분 10개 인덱스만)
    print(f" {name} KO Index Sample: {src_sample[0][:10].tolist()}")
    print(f" {name} EN Index Sample: {tar_sample[0][:10].tolist()}\n")

2026-01-17 13:56:47,622 - Mission11_NMT - INFO - [TRAIN Batch Sample]
2026-01-17 13:56:47,624 - Mission11_NMT - INFO -  - Source Shape (KO): torch.Size([32, 29])
2026-01-17 13:56:47,624 - Mission11_NMT - INFO -  - Target Shape (EN): torch.Size([32, 27])
2026-01-17 13:56:47,627 - Mission11_NMT - INFO - [VALID Batch Sample]
2026-01-17 13:56:47,628 - Mission11_NMT - INFO -  - Source Shape (KO): torch.Size([32, 25])
2026-01-17 13:56:47,628 - Mission11_NMT - INFO -  - Target Shape (EN): torch.Size([32, 25])


 TRAIN KO Index Sample: [33303, 36435, 27262, 25374, 33995, 1214, 21024, 2808, 30854, 2544]
 TRAIN EN Index Sample: [2, 40180, 40366, 40837, 37194, 37203, 19567, 40859, 21897, 6]

 VALID KO Index Sample: [25187, 6, 36134, 29146, 1211, 0, 0, 0, 0, 0]
 VALID EN Index Sample: [2, 26233, 5, 30262, 2447, 3, 0, 0, 0, 0]



* **데이터 로드 자동화:** 전처리된 피클 파일(`nmt_preprocessed_final.pkl`)을 로드하여 1,082,046개의 학습 데이터를 즉각 복원함.
* **Custom Dataset 설계:** 텍스트 토큰을 고유 인덱스로 변환하고, 영어(Target) 문장에는 학습 필수 요소인 `<sos>`와 `<eos>` 토큰을 부착함.
* **배치 처리 및 패딩:** `DataLoader`와 `collate_fn`을 활용하여 배치 사이즈를 64로 설정하고, `MAX_LENGTH`에 맞춰 문장 길이를 통일(Padding)함.

> **이식성 확보:** 전처리 단계를 건너뛰더라도 로거 및 디바이스 설정 후 본 단계부터 즉시 실행 가능한 환경을 구축하여 작업 효율성을 극대화함.

> **정합성 확인:** Train과 Valid 데이터셋 모두 배치 생성이 정상적으로 이루어짐을 확인

# 기본 모멜 (Seq2Seq Baseline)


1. 모델 아키텍처 설계 (Architecture)
- 단방향 GRU 기반 Seq2Seq: Encoder와 Decoder 모두 단방향 GRU(Gated Recurrent Unit)를 사용하는 가장 표준적인 구조로 설계되었습니다.
- Encoder (Context Vector 생성): 입력 문장을 고정된 크기의 **Context Vector(Hidden State)**로 압축합니다. batch_first=True 설정을 통해 데이터 차원의 직관성을 높였습니다.
- Decoder (순차적 생성): Encoder의 마지막 Hidden State를 초기값으로 전달받아 문맥을 유지하며 단어를 생성합니다. 각 시점(time-step)마다 예측된 단어를 다음 시점의 입력으로 사용하는 자기 회귀(Autoregressive) 구조를 가집니다.
- Dimension Handling: 배치 처리를 위해 unsqueeze(1)로 차원을 확장하여 입력을 공급하고, 연산 후 squeeze(1)을 통해 다시 클래시파이어로 전달하는 최적화 로직을 적용했습니다.

2. 통합 모델 및 학습 전략 (Integration & Strategy)
- Randomized Teacher Forcing: 학습 속도 향상을 위해 50%의 확률로 실제 정답(Ground Truth)을 다음 시점의 입력으로 사용하는 Teacher Forcing 기법을 적용했습니다. 평가(Evaluation) 시에는 이를 0으로 설정하여 모델의 순수 생성 능력을 측정합니다.
- 데이터 타입 안정성: Embedding 층의 입력 규격에 맞춰 소스(src)와 타겟(trg) 텐서를 모두 .long() 타입으로 강제 변환하여 데이터 타입 불일치 에러를 방지했습니다.
- 가중치 초기화: nn.init.normal_을 활용하여 가중치를 평균 0, 표준편차 0.01의 정규분포로 초기화하고, 바이어스는 0으로 설정하여 초기 학습의 수렴 안정성을 확보했습니다.

3. 학습 시스템 구축 (Training Environment)
- 하이퍼파라미터: 대규모 코퍼스 학습을 위해 HID_DIM(512), EMB_DIM(256), Dropout(0.5) 등의 파라미터를 설정했습니다.
- 손실 함수 및 최적화: * Padding Masking: ignore_index 설정을 통해 의미 없는 <pad> 토큰이 손실값 계산 및 역전파에 영향을 주지 않도록 마스킹했습니다.
- Gradient Clipping: RNN 계열에서 자주 발생하는 기울기 폭주 현상을 막기 위해 clip 임계값을 설정하여 수치적 안정성을 높였습니다.
- 성능 지표: 단순 Loss 외에도 언어 모델의 직관적 성능 지표인 **PPL(Perplexity)**을 매 에폭마다 산출하여 학습 진행 상황을 모니터링합니다.

In [7]:
import os
import pickle
import torch
import torch.nn as nn
import random
import math
import time
from tqdm import tqdm

# ==========================================
# 1. 모델 클래스 정의 (Encoder, Decoder, Seq2Seq)
# ==========================================

class EncoderBasic(nn.Module):
    def __init__(self, input_dim, emb_dim, hid_dim, n_layers, dropout):
        super().__init__()
        self.embedding = nn.Embedding(input_dim, emb_dim)
        # Basic 모델: 단방향 GRU
        self.rnn = nn.GRU(emb_dim, hid_dim, n_layers, dropout=dropout, batch_first=True)
        self.dropout = nn.Dropout(dropout)
        
    def forward(self, src):
        # src: [batch, seq_len]
        embedded = self.dropout(self.embedding(src))
        outputs, hidden = self.rnn(embedded)
        # Context Vector로 사용할 hidden state만 반환
        return hidden

class DecoderBasic(nn.Module):
    def __init__(self, output_dim, emb_dim, hid_dim, n_layers, dropout):
        super().__init__()
        self.output_dim = output_dim
        self.embedding = nn.Embedding(output_dim, emb_dim)
        # Basic 모델: Attention 없음
        self.rnn = nn.GRU(emb_dim, hid_dim, n_layers, dropout=dropout, batch_first=True)
        self.fc_out = nn.Linear(hid_dim, output_dim)
        self.dropout = nn.Dropout(dropout)
        
    def forward(self, input, hidden, encoder_outputs=None):
        # input: [batch] (단어 1개)
        input = input.unsqueeze(1) # [batch, 1]
        embedded = self.dropout(self.embedding(input))
        
        # RNN 통과 (encoder_outputs 안 씀)
        output, hidden = self.rnn(embedded, hidden)
        
        prediction = self.fc_out(output.squeeze(1))
        return prediction, hidden

class Seq2SeqBasic(nn.Module):
    def __init__(self, encoder, decoder, device):
        super().__init__()
        self.encoder = encoder
        self.decoder = decoder
        self.device = device
        
    def forward(self, src, trg, teacher_forcing_ratio=0.5):
        # src: [batch, src_len], trg: [batch, trg_len]
        batch_size = src.shape[0]
        trg_len = trg.shape[1]
        trg_vocab_size = self.decoder.output_dim
        
        # 결과 저장용 텐서
        outputs = torch.zeros(batch_size, trg_len, trg_vocab_size).to(self.device)
        
        # 인코더: Context Vector 생성
        hidden = self.encoder(src)
        
        # 첫 입력은 <sos> 토큰
        input = trg[:, 0]
        
        for t in range(1, trg_len):
            # 디코더 실행
            output, hidden = self.decoder(input, hidden)
            outputs[:, t] = output
            
            # Teacher Forcing 결정
            teacher_force = random.random() < teacher_forcing_ratio
            top1 = output.argmax(1)
            input = trg[:, t] if teacher_force else top1
            
        return outputs

# ==========================================
# 2. 모델 조립 및 설정
# ==========================================

# 하이퍼파라미터
INPUT_DIM = len(ko_word2idx)
OUTPUT_DIM = len(en_word2idx)
ENC_EMB_DIM = 256
DEC_EMB_DIM = 256
HID_DIM = 512
N_LAYERS = 1
ENC_DROPOUT = 0.5
DEC_DROPOUT = 0.5

# 모델 인스턴스 생성 (변수명: model_basic)
enc_basic = EncoderBasic(INPUT_DIM, ENC_EMB_DIM, HID_DIM, N_LAYERS, ENC_DROPOUT)
dec_basic = DecoderBasic(OUTPUT_DIM, DEC_EMB_DIM, HID_DIM, N_LAYERS, DEC_DROPOUT)
model_basic = Seq2SeqBasic(enc_basic, dec_basic, device).to(device)

# 가중치 초기화 함수
def init_weights(m):
    for name, param in m.named_parameters():
        if 'weight' in name:
            nn.init.normal_(param.data, mean=0, std=0.01)
        else:
            nn.init.constant_(param.data, 0)

model_basic.apply(init_weights)

print(f"✅ Basic Model Created | Params: {sum(p.numel() for p in model_basic.parameters()):,} parameters")

# 1. 손실 함수 정의 (Padding 무시 설정)
# (en_word2idx가 이미 로드되어 있다고 가정합니다)
PAD_IDX = en_word2idx['<pad>']
criterion = nn.CrossEntropyLoss(ignore_index=PAD_IDX)

# 2. 1 Epoch 학습 함수

def train(model, loader, optimizer, criterion, clip):
    model.train()
    epoch_loss = 0
    
    # 1. pbar를 한 번만 정의합니다.
    pbar = tqdm(loader, desc="Training", leave=False)
    
    # 2. for문에 tqdm(loader) 대신 pbar를 넣습니다.
    for i, (src, trg) in enumerate(pbar):
        # .long() 추가 잘 하셨습니다!
        src, trg = src.to(device).long(), trg.to(device).long()
        
        optimizer.zero_grad()
        
        output = model(src, trg)
        
        output_dim = output.shape[-1]
        output = output[:, 1:].reshape(-1, output_dim)
        trg = trg[:, 1:].reshape(-1)
        
        loss = criterion(output, trg)
        loss.backward()
        
        torch.nn.utils.clip_grad_norm_(model.parameters(), clip)
        
        optimizer.step()
        epoch_loss += loss.item()
        
        # 3. 실시간 Loss 업데이트가 이제 정상 작동합니다.
        pbar.set_postfix(loss=f"{loss.item():.4f}")

    return epoch_loss / len(loader)

# 3. 1 Epoch 평가 함수
def evaluate(model, loader, criterion):
    model.eval()
    epoch_loss = 0
    
    with torch.no_grad():
        for i, (src, trg) in enumerate(tqdm(loader, desc="Evaluating", leave=False)):
            src, trg = src.to(device).long(), trg.to(device).long() # <--- .long() 추가
            
            # Teacher Forcing 0으로 설정
            output = model(src, trg, teacher_forcing_ratio=0)
            
            output_dim = output.shape[-1]
            output = output[:, 1:].reshape(-1, output_dim)
            trg = trg[:, 1:].reshape(-1)
            
            loss = criterion(output, trg)
            epoch_loss += loss.item()
            
    return epoch_loss / len(loader)

# 4. 메인 학습 루프 (run_training)
def run_training(model, train_loader, valid_loader, optimizer, criterion, n_epochs, clip, save_dir):
    # 저장 경로 생성
    os.makedirs(save_dir, exist_ok=True)
    
    best_valid_loss = float('inf')
    history = {'train_loss': [], 'valid_loss': []}
    
    print(f"🚀 학습 시작! (Total Epochs: {n_epochs})")
    print("-" * 60)
    
    for epoch in range(n_epochs):
        start_time = time.time()
        
        # 학습 및 평가
        train_loss = train(model, train_loader, optimizer, criterion, clip)
        valid_loss = evaluate(model, valid_loader, criterion)
        
        end_time = time.time()
        epoch_mins, epoch_secs = divmod(int(end_time - start_time), 60)
        
        # 기록
        history['train_loss'].append(train_loss)
        history['valid_loss'].append(valid_loss)
        
        # PPL 계산 (Overflow 방지)
        train_ppl = math.exp(train_loss) if train_loss < 100 else float('inf')
        valid_ppl = math.exp(valid_loss) if valid_loss < 100 else float('inf')
        
        # Best Model 저장
        if valid_loss < best_valid_loss:
            best_valid_loss = valid_loss
            torch.save(model.state_dict(), os.path.join(save_dir, 'best_model.pt'))
            save_msg = "🔥 Best Model Saved"
        else:
            save_msg = ""
            
        print(f'Epoch: {epoch+1:02} | Time: {epoch_mins}m {epoch_secs}s')
        print(f'\tTrain Loss: {train_loss:.3f} | Train PPL: {train_ppl:7.3f}')
        print(f'\t Val. Loss: {valid_loss:.3f} |  Val. PPL: {valid_ppl:7.3f} {save_msg}')
    
    # 히스토리 저장
    with open(os.path.join(save_dir, 'history.pkl'), 'wb') as f:
        pickle.dump(history, f)
    print("✅ 모든 학습 과정이 완료되었습니다.")


e:\github\temp_mission11\.venv\Lib\site-packages\torch\nn\modules\rnn.py:123: UserWarning: dropout option adds dropout after all but last recurrent layer, so non-zero dropout expects num_layers greater than 1, but got dropout=0.5 and num_layers=1
  warnings.warn(


✅ Basic Model Created | Params: 45,794,042 parameters


In [ ]:

# ==========================================
# 학습 실행 (Training Run)
# ==========================================

# Optimizer 설정 (model_basic 전용)
optimizer_basic = torch.optim.Adam(model_basic.parameters(), lr=0.001)

# 학습 설정
N_EPOCHS = 5
CLIP = 1
SAVE_DIR_BASIC = '../model_checkpoints_basic' # 저장 폴더 분리

# 학습 루프 실행
run_training(model_basic, train_loader, valid_loader, optimizer_basic, criterion, N_EPOCHS, CLIP, SAVE_DIR_BASIC)

In [22]:
import pandas as pd
import pickle
import os
import math
from datetime import datetime

# 1. 파일이 저장된 경로 설정 (위에서 설정한 SAVE_DIR_BASIC과 동일해야 함)
SAVE_DIR_BASIC = '../model_checkpoints_basic'
pkl_path = os.path.join(SAVE_DIR_BASIC, 'history.pkl')

# 2. 파일이 존재하는지 확인 후 읽어오기
if os.path.exists(pkl_path):
    with open(pkl_path, 'rb') as f:
        loaded_history = pickle.load(f)
    
    # 3. 데이터프레임 변환
    df_history = pd.DataFrame(loaded_history)
    
    # 4. PPL 계산 (분석용 추가)
    df_history['train_ppl'] = df_history['train_loss'].apply(lambda x: math.exp(x) if x < 100 else float('inf'))
    df_history['valid_ppl'] = df_history['valid_loss'].apply(lambda x: math.exp(x) if x < 100 else float('inf'))
    
    # 5. 모델명 포함 CSV 저장
    model_name = "Basic_RNN_Model"
    current_time = datetime.now().strftime("%m%d_%H%M")
    csv_filename = f"{model_name}_history_{current_time}.csv"
    
    save_path = f'{SAVE_DIR_BASIC}/{csv_filename}'
    df_history.to_csv(save_path, index=False)
    
    logger.info(f"'{save_path}'에 저장 완료.")
    print(df_history) # 결과 확인
else:
    logger.error(f"❌ '{pkl_path}' 파일을 찾을 수 없습니다. 학습이 완전히 끝났었나요?")

2026-01-17 13:35:07,435 - Mission11_NMT - INFO - '../model_checkpoints_basic/Basic_RNN_Model_history_0117_1335.csv'에 저장 완료.


   train_loss  valid_loss  train_ppl  valid_ppl
0    4.279072    4.239467  72.173402  69.370872
1    3.200019    3.933093  24.533007  51.064691
2    2.911192    3.816541  18.378691  45.446728
3    2.759972    3.700282  15.799396  40.458696
4    2.660954    3.656370  14.309939  38.720544


- train_loss, valid_loss 모두 에폭마다 유의미하게 감소
- 에폭수를 늘려서 추가 학습하면 모델 성능이 더욱 향상될 것으로 기대
- 학습시간 리소스와 개선 모델과의 성능 차이를 비교하기 위해 에폭은 진행하지 않음

# 개선 모델: Seq2Seq + Attention (Bahdanau)

1. 모델 아키텍처 설계 (Architecture)
- 양방향(Bidirectional) GRU Encoder: 인코더가 문장을 순방향과 역방향으로 동시에 학습하여 풍부한 문맥 정보를 추출하며, 두 방향의 마지막 은닉 상태를 결합(Concatenate)한 후 $tanh$ 활성화 함수를 거쳐 디코더의 초기값으로 전달합니다.
- Attention Mechanism (Bahdanau Attention): 디코더의 현재 상태와 인코더의 모든 시점 출력값 사이의 유사도를 계산하여 가중치(Softmax)를 산출합니다. 이를 통해 모델이 번역 시 입력 문장의 핵심 단어에 동적으로 집중하게 합니다.
- Attention-Based Decoder: 어텐션 가중치가 적용된 가중합(Weighted Sum) 벡터와 이전 시점의 예측 임베딩을 결합하여 GRU를 연산하며, 최종 출력층에서도 문맥 벡터와 RNN 출력을 모두 활용하여 예측 정확도를 극대화합니다.
- Matrix Operations: torch.bmm(Batch Matrix Multiplication)을 사용하여 배치 단위의 어텐션 연산을 효율적으로 처리하며, 복잡한 텐서 연산(permute, squeeze 등)을 통해 차원 규격을 정밀하게 관리합니다.
2. 통합 모델 및 학습 전략 (Integration & Strategy)
- 전 구간 정보 전달: 인코더의 모든 시점 은닉 상태(encoder_outputs)를 디코더에 상시 공급하여, 고정된 크기의 컨텍스트 벡터가 가지는 정보 손실 문제를 해결했습니다.
- 초기 상태 변환(FC Layer): 인코더의 양방향 합산 차원($enc\_hid\_dim \times 2$)을 디코더의 은닉 차원($dec\_hid\_dim$)으로 정렬하기 위한 선형 변환 층을 배치하여 모델 간 호환성을 확보했습니다.
- Randomized Teacher Forcing: 학습 시에는 50% 확률로 정답을 강제 입력하여 수렴 속도를 높이고, 평가 시에는 모델의 예측값만으로 문장을 생성하도록 설계했습니다.
3. 학습 시스템 구축 (Training Environment)
- 하이퍼파라미터 세분화: 인코더/디코더 은닉 차원(512), 임베딩 차원(256), 드롭아웃(0.5) 등 어텐션 연산에 최적화된 규모로 설정했습니다.
- 가중치 초기화: 모든 선형 층과 RNN 가중치를 평균 0, 표준편차 0.01인 정규분포로 초기화하여 초기 그래디언트의 안정적 흐름을 유도했습니다.
- 손실 함수 및 안정화: * Padding Masking: <pad> 토큰을 무시하도록 ignore_index를 설정하여 유의미한 데이터에 집중했습니다.
    - Gradient Clipping: RNN의 고질적인 문제인 기울기 폭주를 방지하기 위해 $L_2$ 노름 기준 임계값(CLIP=1)을 적용했습니다.
- 성능 지표: 매 에폭마다 **PPL(Perplexity)**과 Loss를 산출하여 모델이 문장을 얼마나 자연스럽게 생성하는지 정량적으로 모니터링합니다.

In [8]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import random

# ---------------------------------------------------------
# 1. Attention Encoder (새로 추가됨!)
#    - 특징: 양방향(Bidirectional), outputs 반환
# ---------------------------------------------------------
class Encoder(nn.Module):
    def __init__(self, input_dim, emb_dim, enc_hid_dim, dec_hid_dim, dropout):
        super().__init__()
        self.embedding = nn.Embedding(input_dim, emb_dim)
        
        # [중요] Attention용은 양방향(bidirectional=True) 사용
        self.rnn = nn.GRU(emb_dim, enc_hid_dim, bidirectional=True, batch_first=True)
        
        # 양방향 Hidden State(Forward + Backward)를 합쳐서 Decoder의 초기 Hidden으로 변환하는 층
        self.fc = nn.Linear(enc_hid_dim * 2, dec_hid_dim)
        self.dropout = nn.Dropout(dropout)
        
    def forward(self, src):
        # src: [batch, src_len]
        embedded = self.dropout(self.embedding(src))
        
        # outputs: [batch, src_len, enc_hid_dim * 2] -> 모든 시점의 은닉 상태 (Attention 계산용)
        # hidden: [2, batch, enc_hid_dim] -> 마지막 시점의 은닉 상태 (Forward, Backward)
        outputs, hidden = self.rnn(embedded)
        
        # Hidden 처리: (Forward + Backward) -> Linear -> Tanh -> Decoder 초기값
        # hidden[-2, :, :] : Forward의 마지막 hidden
        # hidden[-1, :, :] : Backward의 마지막 hidden
        hidden = torch.tanh(self.fc(torch.cat((hidden[-2,:,:], hidden[-1,:,:]), dim=1)))
        
        return outputs, hidden

# ---------------------------------------------------------
# 2. Attention Layer (작성하신 코드 그대로)
# ---------------------------------------------------------
class Attention(nn.Module):
    def __init__(self, enc_hid_dim, dec_hid_dim):
        super().__init__()
        self.attn = nn.Linear((enc_hid_dim * 2) + dec_hid_dim, dec_hid_dim)
        self.v = nn.Linear(dec_hid_dim, 1, bias=False)

    def forward(self, hidden, encoder_outputs):
        batch_size = encoder_outputs.shape[0]
        src_len = encoder_outputs.shape[1]
        
        hidden = hidden.unsqueeze(1).repeat(1, src_len, 1)
        energy = torch.tanh(self.attn(torch.cat((hidden, encoder_outputs), dim=2)))
        attention = self.v(energy).squeeze(2)
        
        return F.softmax(attention, dim=1)

# ---------------------------------------------------------
# 3. Attention Decoder (작성하신 코드 그대로)
# ---------------------------------------------------------
class AttentionDecoder(nn.Module):
    def __init__(self, output_dim, emb_dim, enc_hid_dim, dec_hid_dim, dropout, attention):
        super().__init__()
        self.output_dim = output_dim
        self.attention = attention
        self.embedding = nn.Embedding(output_dim, emb_dim)
        self.rnn = nn.GRU((enc_hid_dim * 2) + emb_dim, dec_hid_dim)
        self.fc_out = nn.Linear((enc_hid_dim * 2) + dec_hid_dim + emb_dim, output_dim)
        self.dropout = nn.Dropout(dropout)

    def forward(self, input, hidden, encoder_outputs):
        input = input.unsqueeze(0) 
        embedded = self.dropout(self.embedding(input)) 
        
        a = self.attention(hidden, encoder_outputs) 
        a = a.unsqueeze(1) 
        
        weighted = torch.bmm(a, encoder_outputs) 
        weighted = weighted.permute(1, 0, 2) 
        
        rnn_input = torch.cat((embedded, weighted), dim=2)
        output, hidden = self.rnn(rnn_input, hidden.unsqueeze(0))
        
        embedded = embedded.squeeze(0)
        output = output.squeeze(0)
        weighted = weighted.squeeze(0)
        
        prediction = self.fc_out(torch.cat((output, weighted, embedded), dim=1))
        
        return prediction, hidden.squeeze(0)

# ---------------------------------------------------------
# 4. 통합 Attention Seq2Seq 모델 (작성하신 코드 그대로)
# ---------------------------------------------------------
class AttentionSeq2Seq(nn.Module):
    def __init__(self, encoder, decoder, device):
        super().__init__()
        self.encoder = encoder
        self.decoder = decoder
        self.device = device

    def forward(self, src, trg, teacher_forcing_ratio=0.5):
        batch_size = src.shape[0]
        trg_len = trg.shape[1]
        trg_vocab_size = self.decoder.output_dim
        outputs = torch.zeros(batch_size, trg_len, trg_vocab_size).to(self.device)
        
        # 인코더: outputs, hidden 두 개 다 받음!
        encoder_outputs, hidden = self.encoder(src)
        
        input = trg[:, 0]
        for t in range(1, trg_len):
            output, hidden = self.decoder(input, hidden, encoder_outputs)
            outputs[:, t] = output
            teacher_force = random.random() < teacher_forcing_ratio
            top1 = output.argmax(1)
            input = trg[:, t] if teacher_force else top1
            
        return outputs

# ---------------------------------------------------------
# 5. 모델 조립
# ---------------------------------------------------------
INPUT_DIM = len(ko_word2idx)
OUTPUT_DIM = len(en_word2idx)
ENC_EMB_DIM = 256
DEC_EMB_DIM = 256
ENC_HID_DIM = 512
DEC_HID_DIM = 512
ENC_DROPOUT = 0.5
DEC_DROPOUT = 0.5

# 인스턴스 생성 (여기서 위에서 만든 Encoder 클래스가 쓰입니다)
attn = Attention(ENC_HID_DIM, DEC_HID_DIM)
enc_attn = Encoder(INPUT_DIM, ENC_EMB_DIM, ENC_HID_DIM, DEC_HID_DIM, ENC_DROPOUT)
dec_attn = AttentionDecoder(OUTPUT_DIM, DEC_EMB_DIM, ENC_HID_DIM, DEC_HID_DIM, DEC_DROPOUT, attn)

model_attn = AttentionSeq2Seq(enc_attn, dec_attn, device).to(device)

def init_weights(m):
    for name, param in m.named_parameters():
        if 'weight' in name:
            nn.init.normal_(param.data, mean=0, std=0.01)
        else:
            nn.init.constant_(param.data, 0)

model_attn.apply(init_weights)

print(f"✅ Attention 모델 조립 완료 | Params: {sum(p.numel() for p in model_attn.parameters()):,}개")

✅ Attention 모델 조립 완료 | Params: 102,938,362개


- 최초 학습 시 오류 발생으로 본 학습 들어가기전에 1배치 추출하여 디버깅 하는 코드 작성

In [15]:
def debug_attention_test(model, loader, device):
    logger.info("🛠️ Phase 4: Attention 모델 디버그 테스트 시작 (1 Batch)")
    model.to(device)
    model.train()
    
    try:
        # 1. 데이터 로더에서 샘플 1개 배치 추출 (2개 샘플만 사용)
        src, trg = next(iter(loader))
        src, trg = src[:2].to(device), trg[:2].to(device)
        
        # 2. 순전파 실행
        optimizer.zero_grad()
        output = model(src, trg)
        
        # 3. 결과 차원 검증
        # output shape: [batch_size, trg_len, output_dim]
        batch_size, trg_len, output_dim = output.shape
        logger.info(f"Input Src Shape: {src.shape}")
        logger.info(f"Input Trg Shape: {trg.shape}")
        logger.info(f"Attention Output Shape: {output.shape}")
        
        # 4. 역전파 테스트 (Loss 계산 가능 여부 확인)
        output_flattened = output[:, 1:].reshape(-1, output_dim)
        trg_flattened = trg[:, 1:].reshape(-1)
        loss = criterion(output_flattened, trg_flattened)
        loss.backward()
        
        logger.info("✅ Attention 모델 구조 및 차원 검증 성공!")
        
    except Exception as e:
        logger.error(f"❌ Attention 모델 테스트 중 오류 발생: {e}")
        import traceback
        logger.error(traceback.format_exc())

# 테스트 실행 (model_attn은 새로 정의한 AttentionSeq2Seq 인스턴스)
debug_attention_test(model_attn, train_loader, device)

2026-01-16 02:37:19,110 - Mission11_NMT - INFO - 🛠️ Phase 4: Attention 모델 디버그 테스트 시작 (1 Batch)
2026-01-16 02:37:19,258 - Mission11_NMT - INFO - Input Src Shape: torch.Size([2, 30])
2026-01-16 02:37:19,259 - Mission11_NMT - INFO - Input Trg Shape: torch.Size([2, 31])
2026-01-16 02:37:19,260 - Mission11_NMT - INFO - Attention Output Shape: torch.Size([2, 31, 41466])
2026-01-16 02:37:19,336 - Mission11_NMT - INFO - ✅ Attention 모델 구조 및 차원 검증 성공!


In [16]:
import time
import math
import os
import pickle
import torch
import torch.nn as nn
from tqdm import tqdm
# [수정 1] 메모리 절약을 위한 라이브러리 추가
from torch.cuda.amp import autocast, GradScaler

# ---------------------------------------------------------
# 1. 학습 및 평가 함수
# ---------------------------------------------------------
def train(model, loader, optimizer, criterion, clip):
    model.train()
    epoch_loss = 0
    
    # [수정 2] Mixed Precision을 위한 Scaler 정의
    scaler = GradScaler()
    
    pbar = tqdm(loader, desc="Training", leave=False)
    for i, (src, trg) in enumerate(pbar):
        src, trg = src.to(device).long(), trg.to(device).long()
        
        optimizer.zero_grad()
        
        # [수정 3] autocast로 연산 정밀도 자동 조절 (메모리 대폭 절약)
        with autocast():
            output = model(src, trg)
            
            output_dim = output.shape[-1]
            output = output[:, 1:].reshape(-1, output_dim)
            trg = trg[:, 1:].reshape(-1)
            
            loss = criterion(output, trg)
        
        # [수정 4] Scaler를 사용한 역전파
        scaler.scale(loss).backward()
        
        # Gradient Clipping (Scaler 사용 시 unscale 먼저 해야 함)
        scaler.unscale_(optimizer)
        torch.nn.utils.clip_grad_norm_(model.parameters(), clip)
        
        # Optimizer Step
        scaler.step(optimizer)
        scaler.update()
        
        epoch_loss += loss.item()
        pbar.set_postfix(loss=f"{loss.item():.4f}")
        
    return epoch_loss / len(loader)

def evaluate(model, loader, criterion):
    model.eval()
    epoch_loss = 0
    
    with torch.no_grad():
        for i, (src, trg) in enumerate(tqdm(loader, desc="Evaluating")):
            src, trg = src.to(device).long(), trg.to(device).long()
            
            # [수정 5] 평가 때도 autocast 쓰면 속도 빨라짐
            with autocast():
                output = model(src, trg, teacher_forcing_ratio=0)
                
                output_dim = output.shape[-1]
                output = output[:, 1:].reshape(-1, output_dim)
                trg = trg[:, 1:].reshape(-1)
                
                loss = criterion(output, trg)
                
            epoch_loss += loss.item()
            
    return epoch_loss / len(loader)

def run_training(model, train_loader, valid_loader, optimizer, criterion, n_epochs, clip, save_dir):
    os.makedirs(save_dir, exist_ok=True)
    best_valid_loss = float('inf')
    history = {'train_loss': [], 'valid_loss': []}
    
    # logger가 정의되어 있지 않다면 print로 대체하세요.
    print(f"🚀 학습 시작! (총 Epochs: {n_epochs})")
    print("-" * 60)

    for epoch in range(n_epochs):
        start_time = time.time()
        
        train_loss = train(model, train_loader, optimizer, criterion, clip)
        valid_loss = evaluate(model, valid_loader, criterion)
        
        end_time = time.time()
        epoch_mins, epoch_secs = divmod(int(end_time - start_time), 60)
        
        history['train_loss'].append(train_loss)
        history['valid_loss'].append(valid_loss)
        
        train_ppl = math.exp(train_loss) if train_loss < 100 else float('inf')
        valid_ppl = math.exp(valid_loss) if valid_loss < 100 else float('inf')
        
        if valid_loss < best_valid_loss:
            best_valid_loss = valid_loss
            torch.save(model.state_dict(), os.path.join(save_dir, 'best_attention_model.pt'))
            save_msg = f"🔥 Best Model Saved"
        else:
            save_msg = ""
            
        print(f'Epoch: {epoch+1:02} | Time: {epoch_mins}m {epoch_secs}s')
        print(f'\tTrain Loss: {train_loss:.3f} | Train PPL: {train_ppl:7.3f}')
        print(f'\t Val. Loss: {valid_loss:.3f} |  Val. PPL: {valid_ppl:7.3f} {save_msg}')
    
    with open(os.path.join(save_dir, 'history.pkl'), 'wb') as f:
        pickle.dump(history, f)
    print("✅ 모든 학습 과정 완료.")
    return history # <-- 나중에 CSV 저장을 위해 추가했습니다.

# ---------------------------------------------------------
# 2. 실행 (실제 학습 시작 전 체크)
# ---------------------------------------------------------

# 이 부분은 본인의 환경에 맞게 변수가 설정되어 있는지 확인하세요.
optimizer = torch.optim.Adam(model_attn.parameters(), lr=0.001)
# 0번이 <pad>인 경우 ignore_index=0 혹은 PAD_IDX를 사용합니다.
criterion = nn.CrossEntropyLoss(ignore_index=0) 

N_EPOCHS = 5
CLIP = 1
SAVE_DIR = '../model_checkpoints_attention' 

# 학습 실행
history_attn = run_training(model_attn, train_loader, valid_loader, optimizer, criterion, N_EPOCHS, CLIP, SAVE_DIR)

C:\Users\dbcjf\AppData\Local\Temp\ipykernel_14856\538583315.py:19: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  scaler = GradScaler()


🚀 학습 시작! (총 Epochs: 5)
------------------------------------------------------------


Training:   0%|          | 0/33814 [00:00<?, ?it/s]C:\Users\dbcjf\AppData\Local\Temp\ipykernel_14856\538583315.py:28: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with autocast():
Evaluating:   0%|          | 0/4426 [00:00<?, ?it/s]                            C:\Users\dbcjf\AppData\Local\Temp\ipykernel_14856\538583315.py:62: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with autocast():
Evaluating: 100%|██████████| 4426/4426 [12:31<00:00,  5.89it/s]


Epoch: 01 | Time: 286m 16s
	Train Loss: 3.348 | Train PPL:  28.451
	 Val. Loss: 3.802 |  Val. PPL:  44.792 🔥 Best Model Saved


Evaluating: 100%|██████████| 4426/4426 [12:34<00:00,  5.86it/s]                 


...

Epoch: 03 | Time: 288m 16s
	Train Loss: 2.653 | Train PPL:  14.197
	 Val. Loss: 3.724 |  Val. PPL:  41.411 


Evaluating: 100%|██████████| 4426/4426 [12:32<00:00,  5.88it/s]                 


Epoch: 04 | Time: 285m 14s
	Train Loss: 2.588 | Train PPL:  13.304
	 Val. Loss: 3.724 |  Val. PPL:  41.425 


Evaluating: 100%|██████████| 4426/4426 [12:31<00:00,  5.89it/s]                 

Epoch: 05 | Time: 284m 19s
	Train Loss: 2.583 | Train PPL:  13.240
	 Val. Loss: 3.733 |  Val. PPL:  41.813 
✅ 모든 학습 과정 완료.


In [18]:
import pandas as pd
from datetime import datetime


# 2. 결과 저장 로직
try:
    # pickle로 저장된 history 불러오기 (함수 내부에서 저장한 파일)
    history_path = os.path.join(SAVE_DIR, 'history.pkl')
    with open(history_path, 'rb') as f:
        history_data = pickle.load(f)

    # 3. 모델 식별 및 파일명 설정
    model_identifier = "Attention_Seq2Seq" # 모델 구분명
    current_time = datetime.now().strftime("%m%d_%H%M")
    csv_filename = f"{model_identifier}_history_{current_time}.csv"

    # 4. 데이터프레임 변환 및 저장
    df_history = pd.DataFrame(history_data)
    # PPL 계산 열 추가 (분석 편의용)
    df_history['train_ppl'] = df_history['train_loss'].apply(lambda x: math.exp(x))
    df_history['valid_ppl'] = df_history['valid_loss'].apply(lambda x: math.exp(x))
    
    csv_save_path = os.path.join(SAVE_DIR, csv_filename)
    df_history.to_csv(csv_save_path, index=False)

    # [수정] print 대신 logger 사용
    logger.info(f"✨ [{model_identifier}] 리포트 저장 완료!")
    logger.info(f"📍 저장 경로: {csv_save_path}")
    
    # 마지막 에폭 결과 요약 출력 (데이터프레임을 문자열로 변환하여 출력)
    logger.info("\n" + df_history.tail().to_string())

except FileNotFoundError:
    logger.error("❌ history.pkl 파일을 찾을 수 없습니다. 학습이 정상적으로 완료되었는지 확인해주세요.")
except Exception as e:
    logger.error(f"❌ 저장 중 오류 발생: {e}")

2026-01-17 13:20:30,758 - Mission11_NMT - INFO - ✨ [Attention_Seq2Seq] 리포트 저장 완료!


2026-01-17 13:20:30,764 - Mission11_NMT - INFO - 📍 저장 경로: ../model_checkpoints_attention\Attention_Seq2Seq_history_0117_1320.csv
2026-01-17 13:20:30,767 - Mission11_NMT - INFO - 
   train_loss  valid_loss  train_ppl  valid_ppl
0    3.348193    3.802022  28.451285  44.791660
1    2.778989    3.706212  16.102727  40.699335
2    2.653006    3.723558  14.196655  41.411459
3    2.588027    3.723888  13.303504  41.425157
4    2.583216    3.733213  13.239649  41.813218


- 24시간 이상 학습 시간 소요
- 그러나 3에폭 부터는 Train_Loss만 낮아짐
- Train PPL (13.24): 모델이 학습 데이터에 대해서는 문맥을 아주 잘 파악하고 있음
- Valid PPL (41.81): 수치 자체는 나쁘지 않지만, Train PPL과의 격차가 벌어지는 것으로 보아 모델의 복잡도에 비해 데이터가 더 필요하거나 드롭아웃 등의 규제가 조금 더 강했어도 좋았을 것 같음

# 성능 비교

In [12]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import pandas as pd
import glob
from nltk.translate.bleu_score import sentence_bleu, SmoothingFunction

# ==========================================
# 1. [시각화] Plotly 인터랙티브 그래프
# ==========================================
def plot_results_plotly():
    try:
        # 가장 최신 CSV 파일 자동 검색
        b_csv = glob.glob('../model_checkpoints_basic/*.csv')[-1]
        a_csv = glob.glob('../model_checkpoints_attention/*.csv')[-1]
        
        df_b = pd.read_csv(b_csv)
        df_a = pd.read_csv(a_csv)
        
        # Epoch 인덱스 (1부터 시작하도록 조정)
        epochs = list(range(1, len(df_b) + 1))
        
        # 서브플롯 생성 (1행 2열)
        fig = make_subplots(
            rows=1, cols=2,
            subplot_titles=("Validation Loss Comparison", "Validation PPL (Log Scale)"),
            horizontal_spacing=0.15
        )

        # --- (1) Validation Loss ---
        # Basic RNN
        fig.add_trace(go.Scatter(
            x=epochs, y=df_b['valid_loss'],
            mode='lines+markers', name='Basic RNN',
            line=dict(color='royalblue', dash='dash'),
            legendgroup='group1'
        ), row=1, col=1)
        
        # Attention RNN
        fig.add_trace(go.Scatter(
            x=epochs, y=df_a['valid_loss'],
            mode='lines+markers', name='Attention RNN',
            line=dict(color='firebrick', width=3),
            legendgroup='group1'
        ), row=1, col=1)

        # --- (2) Validation PPL ---
        # Basic RNN
        fig.add_trace(go.Scatter(
            x=epochs, y=df_b['valid_ppl'],
            mode='lines+markers', name='Basic RNN',
            line=dict(color='royalblue', dash='dash'),
            legendgroup='group2', showlegend=False
        ), row=1, col=2)
        
        # Attention RNN
        fig.add_trace(go.Scatter(
            x=epochs, y=df_a['valid_ppl'],
            mode='lines+markers', name='Attention RNN',
            line=dict(color='firebrick', width=3),
            legendgroup='group2', showlegend=False
        ), row=1, col=2)

        # 레이아웃 업데이트
        fig.update_layout(
            title_text="Model Performance Analysis: Basic vs Attention",
            height=500, width=1100,
            template="plotly_white",
            hovermode="x unified" # 마우스 오버 시 X축 기준 비교
        )
        
        # Y축 스케일 설정 (PPL은 로그 스케일)
        fig.update_yaxes(title_text="Loss", row=1, col=1)
        fig.update_yaxes(type="log", title_text="PPL", row=1, col=2)
        fig.update_xaxes(title_text="Epoch", row=1, col=1)
        fig.update_xaxes(title_text="Epoch", row=1, col=2)

        fig.show()
        
    except Exception as e:
        print(f"⚠️ 그래프 생성 실패: {e}")


# ==========================================
# 실행
# ==========================================

# 1. Plotly 그래프 그리기
plot_results_plotly()

- 수렴 속도 및 성능: Attention 모델이 Basic 모델보다 훨씬 낮은 지점에서 학습을 시작하며 초기 성능 우위를 점함. 이는 어텐션 메커니즘이 입력 문장의 정보를 고정된 크기의 벡터에 압축해야 하는 '정보 병목(Information Bottleneck)' 현상을 효과적으로 해결했음을 보여줌

- Attention 모델 과적합 : Attention 모델은 에폭 2에서 최저 Validation Loss(~3.71)를 기록한 후 점진적으로 상승하는 과적합 양상을 보임. 반면, Basic 모델은 5에폭까지 꾸준히 손실 값이 하락하며 안정적인 학습 곡선을 그림

> GPU가 긴 학습으로 꼬여있어, 커널 재시작을 해도 재대로 동작하지 않고 에러가 남. CPU로 변경하여 테스트 번역을 진행함

In [17]:
import torch
import torch.nn as nn
import pandas as pd
import os
import pickle
import glob
from nltk.translate.bleu_score import sentence_bleu, SmoothingFunction

# ==========================================
# 1. 무조건 CPU 사용 설정
# ==========================================
device = torch.device('cpu')
print(f"✅ 안전 모드: {device}를 사용하여 평가를 진행합니다.")

# ==========================================
# 2. 데이터 및 단어장 로드
# ==========================================
DATA_DIR = r'E:\github\temp_mission11\data'
PICKLE_PATH = os.path.join(DATA_DIR, 'nmt_preprocessed_final.pkl')

if os.path.exists(PICKLE_PATH):
    with open(PICKLE_PATH, 'rb') as f:
        loaded_data = pickle.load(f)
    ko_word2idx = loaded_data['ko_word2idx']
    en_word2idx = loaded_data['en_word2idx']
    en_idx2word = loaded_data['en_idx2word']
    valid_df = loaded_data['valid_df']
else:
    raise FileNotFoundError("피클 파일을 찾을 수 없습니다.")

# ==========================================
# 3. 모델 CPU 모드로 재빌드
# ==========================================
# 하이퍼파라미터
INPUT_DIM, OUTPUT_DIM = len(ko_word2idx), len(en_word2idx)
ENC_EMB_DIM, DEC_EMB_DIM, HID_DIM = 256, 256, 512
N_LAYERS, DROPOUT = 1, 0.5

# --- Basic Model (CPU) ---
enc_b = EncoderBasic(INPUT_DIM, ENC_EMB_DIM, HID_DIM, N_LAYERS, DROPOUT)
dec_b = DecoderBasic(OUTPUT_DIM, DEC_EMB_DIM, HID_DIM, N_LAYERS, DROPOUT)
# .to(device)가 핵심입니다 (CPU로 보냄)
model_basic_cpu = Seq2SeqBasic(enc_b, dec_b, device).to(device)

# --- Attention Model (CPU) ---
attn_layer = Attention(HID_DIM, HID_DIM)
enc_a = Encoder(INPUT_DIM, ENC_EMB_DIM, HID_DIM, HID_DIM, DROPOUT)
dec_a = AttentionDecoder(OUTPUT_DIM, DEC_EMB_DIM, HID_DIM, HID_DIM, DROPOUT, attn_layer)
# .to(device)가 핵심입니다 (CPU로 보냄)
model_attn_cpu = AttentionSeq2Seq(enc_a, dec_a, device).to(device)

# ==========================================
# 4. 가중치 로드 (CPU 매핑 필수)
# ==========================================
def load_cpu_weights(model, path):
    if os.path.exists(path):
        # map_location='cpu'가 에러를 방지하는 핵심입니다
        model.load_state_dict(torch.load(path, map_location='cpu'))
        model.eval()
        print(f"📂 CPU 로드 성공: {os.path.basename(path)}")
    else:
        print(f"⚠️ 파일 없음: {path}")

load_cpu_weights(model_basic_cpu, '../model_checkpoints_basic/best_model.pt')
load_cpu_weights(model_attn_cpu, '../model_checkpoints_attention/best_attention_model.pt')

# ==========================================
# 5. 번역 함수 (CPU 텐서 사용)
# ==========================================
def translate_cpu(model, src_tokens, max_len=40):
    model.eval()
    # 1. 소스 문장 텐서화
    src_idx = [ko_word2idx.get(t, ko_word2idx.get('<unk>', 0)) for t in src_tokens]
    src_tensor = torch.LongTensor(src_idx).unsqueeze(0).to(device)

    # 2. [핵심 수정] 영어 <sos> 인덱스로 시작하는 더미 타겟 생성
    sos_idx = en_word2idx.get('<sos>', 0)
    # Basic 모델의 에러를 방지하기 위해 영어 단어장 범위를 준수하는 더미 생성
    dummy_trg = torch.full((1, max_len), sos_idx).long().to(device)

    with torch.no_grad():
        # 3. 모델 추론 (두 모델 모두 dummy_trg를 사용하여 안전하게 연산)
        output = model(src_tensor, dummy_trg, teacher_forcing_ratio=0)
        output = output.squeeze(0).argmax(1)

    # 4. 결과 단어 복원
    decoded_words = []
    for idx in output:
        idx = idx.item()
        word = en_idx2word.get(idx, '<unk>')
        if word == '<eos>': break
        if word not in ['<sos>', '<pad>']:
            decoded_words.append(word)
            
    return decoded_words

# ==========================================
# 6. 결과 비교 테이블 생성
# ==========================================
def compare_translations_df(model_basic, model_attn, valid_df, n_samples=10):
    samples = valid_df.sample(n_samples)
    smooth = SmoothingFunction().method1
    results = []
    
    print(f"🔄 분석 시작 ({n_samples}개 샘플)...")
    
    for _, row in samples.iterrows():
        # CPU 함수 사용
        p_basic = translate_cpu(model_basic, row['ko_tokens'])
        p_attn = translate_cpu(model_attn, row['ko_tokens'])
        
        b_score = sentence_bleu([row['en_tokens']], p_basic, smoothing_function=smooth)
        a_score = sentence_bleu([row['en_tokens']], p_attn, smoothing_function=smooth)
        
        results.append({
            'Source': " ".join(row['ko_tokens']),
            'Target': row['en_clean'],
            'Basic': " ".join(p_basic),
            'Attention': " ".join(p_attn),
            'Basic BLEU': round(b_score, 4),
            'Attn BLEU': round(a_score, 4),
            'Winner': 'Attention' if a_score > b_score else 'Basic'
        })
    
    return pd.DataFrame(results)

# 실행 및 출력
df_result = compare_translations_df(model_basic_cpu, model_attn_cpu, valid_df, n_samples=10)

from IPython.display import display
pd.set_option('display.max_colwidth', None)
display(df_result)


✅ 안전 모드: cpu를 사용하여 평가를 진행합니다.


e:\github\temp_mission11\.venv\Lib\site-packages\torch\nn\modules\rnn.py:123: UserWarning:

dropout option adds dropout after all but last recurrent layer, so non-zero dropout expects num_layers greater than 1, but got dropout=0.5 and num_layers=1

C:\Users\dbcjf\AppData\Local\Temp\ipykernel_22292\2830937267.py:58: FutureWarning:

You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you 

📂 CPU 로드 성공: best_model.pt
📂 CPU 로드 성공: best_attention_model.pt
🔄 분석 시작 (10개 샘플)...


Source  \
0                                                           장소 는 부산 에서 열리 는 국제 식품 박람회 입니다 .   
1  필요 하 신 경우 잠재 고객 들 에게 상품 에 대한 정보 를 제공 하 는 팜플렛 제작 을 위탁 할 수 있 는 인쇄 업체 를 알선 해 드릴 수 도 있 습니다 .   
2                                                         따라서 정확 한 주문 배송 이 매우 중요 한 사항 입니다 .   
3                                        이 가격 은 이번 달 까지 이 며 만일 기한 을 넘기 면 가격 이 달라질 수 있 습니다 .   
4                                            오늘 오후 6 시 이전 에 주문 해 주 시 면 내일 받 아 보 실 수 있 습니다 .   
5                                                                         무엇 을 어떻게 도와드릴까요 ?   
6                                                                                  이거 좋 다 .   
7                                             이번 음반 은 협주곡 이 아닌 작곡가 1 의 소나타 전집 으로 제작 되 었 습니다   
8                           마지막 으로 , 저희 가 거기 에 머무 는 동안 볼 수 있 는 지역 공연 을 추천 해 주 실 수 있 으신 가요 ?   
9                                                                                    계속 가 .   

                                                                                                                                                                 Target  \
0                                                                                                    the location will be at the international food fair held in busan.   
1  if necessary, we can also arrange a printing company that can entrust the production of pamphlets that provide information about the product to potential customers.   
2                                                                                                                 therefore, accurate order delivery is very important.   
3                                                                                     this price is due this month and the price may change if it exceeds the deadline.   
4                                                                                                            if you order before 6 p.m. today, you can get it tomorrow.   
5                                                                                                                                                   how can i help you?   
6                                                                                                                                                         this is good.   
7                                                                                    this album is not a concerto, but a complete collection of composer aaa 1s sonata.   
8                                                                                lastly, can you recommend a local performance that we can watch during our stay there?   
9                                                                                                                                                           keep going.   

                                                                                                                Basic  \
0                                                the place is a international food fair held by busan international .   
1  if necessary , we can provide a necessary for the products that can produce products necessary for the customers .   
2                                                   therefore , important delivery is important important important .   
3                                                 this price is the price , and the deadline is be the the deadline .   
4                                                        if you order it today before 6 p.m. today , you can get it .   
5                                                                                              how can you help you ?   
6                                                                                                      this is good .   
7                                      this album was made of a <unk> of not a , not a composer of a <unk> composer .   
8                                     finally , can you recommend a 

- 문맥 이해와 단어 선택의 정확도 : 샘플 0번에서 "장소"를 Basic은 단순히 "place"로 번역한 반면, Attention은 비즈니스 문맥에 더 적합한 "venue"를 선택했습니다. 샘플 3번에서도 "달라질 수 있다"를 "may vary"로 번역하며 훨씬 자연스러운 영어 표현을 구사합니다
- 긴 문장 번역: 샘플 인덱스 1번 문장처럼, 장문인 경우 BLEU 스코어의 차이가 더 확연하게 벌어짐
- 과적합 및 반복 생성 문제 : Attention 모델의 BLEU가 전반적으로 높지만, 샘플 1번의 "customers customers"나 샘플 4번의 "tomorrow tomorrow"처럼 특정 단어를 중복해서 생성하는 경향이 관찰됩니다.

In [13]:
from nltk.translate.bleu_score import corpus_bleu

def calculate_corpus_bleu(model, df, name="Model"):
    model.eval()
    references = [] # 실제 정답 토큰 리스트들을 담을 리스트
    hypotheses = [] # 모델이 예측한 토큰 리스트들을 담을 리스트
    
    print(f"🧐 {name} 전체 데이터(총 {len(df)}개) BLEU 계산 시작...")
    
    with torch.no_grad():
        for _, row in tqdm(df.iterrows(), total=len(df), desc=f"{name} Scoring"):
            # 1. 실제 정답 리스트 (corpus_bleu는 [ [ref1], [ref2] ] 형태를 원함)
            references.append([row['en_tokens']])
            
            # 2. 모델 번역 수행
            prediction = translate_cpu(model, row['ko_tokens']) # 앞서 만든 CPU 추론 함수 사용
            hypotheses.append(prediction)
    
    # 전체 코퍼스에 대한 BLEU 점수 계산
    score = corpus_bleu(references, hypotheses, smoothing_function=SmoothingFunction().method1)
    return score * 100

# ---------------------------------------------------------
# 실행 (전체 데이터를 돌리므로 시간이 조금 걸릴 수 있습니다)
# ---------------------------------------------------------

# 1. Basic 모델 전체 점수
basic_total_bleu = calculate_corpus_bleu(model_basic_cpu, valid_df, name="Basic RNN")

# 2. Attention 모델 전체 점수
attn_total_bleu = calculate_corpus_bleu(model_attn_cpu, valid_df, name="Attention RNN")

print(f"\n🏆 [최종 정량 평가 결과]")
print(f"✅ Basic Model Corpus BLEU: {basic_total_bleu:.2f}")
print(f"✅ Attn  Model Corpus BLEU: {attn_total_bleu:.2f}")
print(f"🚀 성능 개선 폭: {attn_total_bleu - basic_total_bleu:.2f} points")

🧐 Basic RNN 전체 데이터(총 141607개) BLEU 계산 시작...


Basic RNN Scoring:   0%|          | 17/141607 [00:00<1:54:08, 20.67it/s]


IndexError: index out of range in self

- 테스트 데이터 전체로 평균 BLEU Score를 비교하여야 하나 리소스 부족으로 보류

In [ ]:
# 2,000개 정도만 샘플링해서 성능 차이를 확인
sample_valid_df = valid_df.sample(2000, random_state=42)

# 1. Basic 모델 샘플 BLEU 점수
basic_sample_bleu = calculate_corpus_bleu(model_basic_cpu, sample_valid_df, name="Basic RNN (Sample)")

# 2. Attention 모델 샘플 BLEU 점수
attn_sample_bleu = calculate_corpus_bleu(model_attn_cpu, sample_valid_df, name="Attention RNN (Sample)")

print(f"\n🏆 [샘플링 평가 결과]")
print(f"✅ Basic Model Sample BLEU: {basic_sample_bleu:.2f}")
print(f"✅ Attn  Model Sample BLEU: {attn_sample_bleu:.2f}")

🧐 Basic RNN (Sample) 전체 데이터(총 2000개) BLEU 계산 시작...


Basic RNN (Sample) Scoring: 100%|██████████| 2000/2000 [05:40<00:00,  5.88it/s]


🧐 Attention RNN (Sample) 전체 데이터(총 2000개) BLEU 계산 시작...


Attention RNN (Sample) Scoring: 100%|██████████| 2000/2000 [18:53<00:00,  1.76it/s]



🏆 [샘플링 평가 결과]
✅ Basic Model Sample BLEU: 19.04
✅ Attn  Model Sample BLEU: 20.16


> 해당 샘플링 또한, 문장길이/서브 카테고리 등을 고려하여 데이터셋을 구성하였어야 하나 지나친 시간 딜레이를 고려하여 이정도로 마무리함

- Attention의 우위: 모델이 소스 문장의 모든 시점을 참조함으로써 정보 압축 손실을 성공적으로 보완했음을 입증

- 추론 속도 차이: Basic 모델(5.88it/s)이 Attention 모델(1.76it/s)보다 약 3.3배 빠른 추론 속도를 보임

# 결론 및 회고

### 결론

> 단순 RNN 기반 Seq2Seq의 한계를 Attention 도입으로 극복했음을 정량적(BLEU), 정성적(번역 품질) 지표로 증명   

추후 개선
1. 과적합 제어: Attention 모델의 손실 값이 튀는 현상을 막기 위해 더 강력한 드롭아웃(Dropout)이나 데이터 증강(Data Augmentation)이 필요
2. 디코딩 전략: 정성 평가에서 확인한, "tomorrow tomorrow"와 같은 중복 생성 문제를 해결하기 위해 Beam Search나 Length Penalty 기법 도입을 고려해 볼 수 있음

### 회고

1. 리소스 문제가 가장 컸음, 기껏 깔끔하게 정리해둔 코드를 관련 문제를 해결하기 위해 더티코드로 덮어쓰고 프로젝트를 급하게 마무리함. 리소스를 고려해 일부 데이터만 이용하는 것으로 전체 프로젝트를 진행하는 것이 다양한 번역 모델 학습을 실습하기에는 좋았을 것이라고 생각
2. 그럼에도, 맥북(M1)/Lambda Labs 원격 컴퓨팅(a10)/윈도우 로컬 데스크탑 환경(1070ti) 을 사용하여 시도해봤다는 점에 의의가 있음. 이후 원격 컴퓨팅을 다시 시도한다면 서버 차단을 고려한 nohup, tmux와 데이터 업로드/다운로드를 고려한 작업이 필수적일 것으로 판단함